In [1]:
import pandas as pd
import json
from datetime import datetime

In [2]:
# red in a table of state populations
populations = pd.read_csv('state_populations.csv',index_col=0).T
populations

state  pop_2014
AL               Alabama   4849377
AK                Alaska    736732
AZ               Arizona   6731484
AR              Arkansas   2966369
CA            California  38802500
CO              Colorado   5355866
CT           Connecticut   3596677
DE              Delaware    935614
DC  District of Columbia    658893
FL               Florida  19893297
GA               Georgia  10097343
HI                Hawaii   1419561
ID                 Idaho   1634464
IL              Illinois  12880580
IN               Indiana   6596855
IA                  Iowa   3107126
KS                Kansas   2904021
KY              Kentucky   4413457
LA             Louisiana   4649676
ME                 Maine   1330089
MD              Maryland   5976407
MA         Massachusetts   6745408
MI              Michigan   9909877
MN             Minnesota   5457173
MS           Mississippi   2994079
MO              Missouri   6063589
MT               Montana   1023579
NE              Nebraska   1881503
NV                Nevada   2839099
NH         New Hampshire   1326813
NJ            New Jersey   8938175
NM            New Mexico   2085572
NY              New York  19746227
NC        North Carolina   9943964
ND          North Dakota    739482
OH                  Ohio  11594163
OK              Oklahoma   3878051
OR                Oregon   3970239
PA          Pennsylvania  12787209
RI          Rhode Island   1055173
SC        South Carolina   4832482
SD          South Dakota    853175
TN             Tennessee   6549352
TX                 Texas  26956958
UT                  Utah   2942902
VT               Vermont    626562
VA              Virginia   8326289
WA            Washington   7061530
WV         West Virginia   1850326
WI             Wisconsin   5757564
WY               Wyoming    584153

In [3]:
# read the data
data = pd.read_csv( 'SlateGunDeaths.csv').fillna(0)
# fix a typo in the state names for consistency
data['state'] = data['state'].apply(lambda x: x.upper())
data

victimID        date                name gender   age  ageGroup  \
0             1  2012-12-14    Antida Archuleta      F  20.0       3.0   
1             2  2012-12-14     Charlotte Bacon      F   6.0       1.0   
2             3  2012-12-14        Olivia Engel      F   6.0       1.0   
3             4  2012-12-14  Ana Marquez-Greene      F   6.0       1.0   
4             5  2012-12-14       Dylan Hockley      M   6.0       1.0   
...         ...         ...                 ...    ...   ...       ...   
12065     13303  2013-12-31                   0      M   0.0       3.0   
12066     13305  2013-12-31                   0      F  43.0       3.0   
12067     13307  2013-12-31    Damien Toney Jr.      M  20.0       3.0   
12068     13308  2013-12-31        Donald Eason      M  22.0       3.0   
12069     13309  2013-12-31                   0      M   0.0       3.0   

              city state        lat         lng  \
0      Westminster    CO  39.893668 -105.072112   
1          Newtown    CT  41.412323  -73.311424   
2          Newtown    CT  41.412323  -73.311424   
3          Newtown    CT  41.412323  -73.311424   
4          Newtown    CT  41.412323  -73.311424   
...            ...   ...        ...         ...   
12065       Camden    NJ  39.944844  -75.119869   
12066      Andover    MN  45.233298  -93.291341   
12067   Santa Rosa    CA  38.405884 -122.794477   
12068    Baltimore    MD  39.290861  -76.610807   
12069    Riverside    CA  33.953355 -117.396162   

                                                     url  
0      http://www.9news.com/rss/story.aspx?storyid=30...  
1      http://www.cnn.com/2012/12/15/us/connecticut-s...  
2      http://www.cnn.com/2012/12/15/us/connecticut-s...  
3      http://www.cnn.com/2012/12/15/us/connecticut-s...  
4      http://www.cnn.com/2012/12/15/us/connecticut-s...  
...                                                  ...  
12065  http://www.nj.com/camden/index.ssf/2013/12/2_s...  
12066  http://www.startribune.com/local/north/2382350...  
12067  http://www.sfgate.com/crime/article/Man-shot-t...  
12068  http://www.baltimoresun.com/news/maryland/crim...  
12069  http://losangeles.cbslocal.com/2013/12/31/man-...  

[12070 rows x 11 columns]

In [4]:
# get county population
countypopulation = pd.read_csv('countrydata.csv')
countypopulation.rename(columns={"County": "county_name"}, inplace=True)
countypopulation.rename(columns={"Population": "population"}, inplace=True)
countypopulation = countypopulation[['county_name', 'population']]
countypopulation['county_name'] = countypopulation['county_name'].str.replace(' County', '')
countypopulation

county_name  population
0        Autauga       59095
1        Baldwin      239294
2        Barbour       24964
3           Bibb       22477
4         Blount       59041
...          ...         ...
3089  Sweetwater       41614
3090       Teton       23575
3091       Uinta       20635
3092    Washakie        7705
3093      Weston        6745

[3094 rows x 2 columns]

In [5]:
# connect with city data
county = pd.read_csv('uscities.csv')
county.rename(columns={"state_id": "state"}, inplace=True)
county = county[['city','county_name', 'state_name', 'state',]]
county = pd.merge(county, countypopulation, on='county_name', how="inner", suffixes=('_x', '_y'))
county

city     county_name  state_name state  \
0                         New York          Queens    New York    NY   
1                           Queens          Queens    New York    NY   
2                      Los Angeles     Los Angeles  California    CA   
3                       Long Beach     Los Angeles  California    CA   
4                        Lancaster     Los Angeles  California    CA   
...                            ...             ...         ...   ...   
139935                      Arthur          Arthur    Nebraska    NE   
139936                Charles City    Charles City    Virginia    VA   
139937  King and Queen Court House  King and Queen    Virginia    VA   
139938                  Harrisburg          Banner    Nebraska    NE   
139939                     Mentone          Loving       Texas    TX   

        population  
0            13075  
1            13075  
2          9829544  
3          9829544  
4          9829544  
...            ...  
139935         439  
139936        6594  
139937        6662  
139938         692  
139939          57  

[139940 rows x 5 columns]

In [6]:
# process dates into individual day, month, year and ordinal timestamp to make sorting and filtering easier
dates = data['date'].apply(lambda x: datetime.strptime(x,'%Y-%m-%d'))
data['year'] = dates.apply(lambda x: x.year)
data['day'] = dates.apply(lambda x: x.day)
data['month'] = dates.apply(lambda x: x.month)
data['timestamp'] = dates.apply(lambda x: x.date().toordinal())
# merge with data for get whole victim information
data = pd.merge(data, county, on=['city', 'state'], how="inner", suffixes=('_x', '_y'))
data

victimID        date                name gender   age  ageGroup  \
0             1  2012-12-14    Antida Archuleta      F  20.0       3.0   
1             1  2012-12-14    Antida Archuleta      F  20.0       3.0   
2             1  2012-12-14    Antida Archuleta      F  20.0       3.0   
3             1  2012-12-14    Antida Archuleta      F  20.0       3.0   
4             1  2012-12-14    Antida Archuleta      F  20.0       3.0   
...         ...         ...                 ...    ...   ...       ...   
48171     13295  2013-12-31  Ricky Junior Toney      M  34.0       3.0   
48172     13295  2013-12-31  Ricky Junior Toney      M  34.0       3.0   
48173     13295  2013-12-31  Ricky Junior Toney      M  34.0       3.0   
48174     13295  2013-12-31  Ricky Junior Toney      M  34.0       3.0   
48175     13305  2013-12-31                   0      F  43.0       3.0   

              city state        lat         lng  \
0      Westminster    CO  39.893668 -105.072112   
1      Westminster    CO  39.893668 -105.072112   
2      Westminster    CO  39.893668 -105.072112   
3      Westminster    CO  39.893668 -105.072112   
4      Westminster    CO  39.893668 -105.072112   
...            ...   ...        ...         ...   
48171    Louisburg    NC  36.099039  -78.301106   
48172    Louisburg    NC  36.099039  -78.301106   
48173    Louisburg    NC  36.099039  -78.301106   
48174    Louisburg    NC  36.099039  -78.301106   
48175      Andover    MN  45.233298  -93.291341   

                                                     url  year  day  month  \
0      http://www.9news.com/rss/story.aspx?storyid=30...  2012   14     12   
1      http://www.9news.com/rss/story.aspx?storyid=30...  2012   14     12   
2      http://www.9news.com/rss/story.aspx?storyid=30...  2012   14     12   
3      http://www.9news.com/rss/story.aspx?storyid=30...  2012   14     12   
4      http://www.9news.com/rss/story.aspx?storyid=30...  2012   14     12   
...                                                  ...   ...  ...    ...   
48171  http://www.wral.com/authorities-shoot-man-want...  2013   31     12   
48172  http://www.wral.com/authorities-shoot-man-want...  2013   31     12   
48173  http://www.wral.com/authorities-shoot-man-want...  2013   31     12   
48174  http://www.wral.com/authorities-shoot-man-want...  2013   31     12   
48175  http://www.startribune.com/local/north/2382350...  2013   31     12   

       timestamp county_name      state_name  population  
0         734851       Adams        Colorado      522140  
1         734851       Adams        Colorado        4625  
2         734851       Adams        Colorado       64954  
3         734851       Adams        Colorado       35961  
4         734851       Adams        Colorado        3641  
...          ...         ...             ...         ...  
48171     735233    Franklin  North Carolina       10464  
48172     735233    Franklin  North Carolina       50325  
48173     735233    Franklin  North Carolina       54938  
48174     735233    Franklin  North Carolina       96749  
48175     735233       Anoka       Minnesota      367018  

[48176 rows x 18 columns]

In [7]:
# loop through the data get aggregated statistics
statedata = []
citydata = []
countydata = []

# groupby returns a touple (key, dataframe[dataframe.groubyargument == key])
for state, statedf in data.groupby('state'):
    # get state information
    all_ids = statedf['victimID'].values.tolist()
    # remove spaces from the state name so it's easier to use as a lookup key in jquery-style selectors later on
    statename = populations.loc[state.upper()]['state'].replace(' ','_')
    state_male_count = statedf[statedf.gender == 'M'].shape[0]
    state_entry = {
        'population': populations.loc[state.upper()]['pop_2014'],
        'abreviation': state,
        'state': statename,
        'count': statedf.shape[0],
        'male_count': state_male_count,
        'ids': all_ids
    }
    statedata.append(state_entry)
    # loop through each wcity within the state
    for city, citydf in statedf.groupby('city'):
        lat = citydf.iloc[0]['lat']
        lng = citydf.iloc[0]['lng']
        all_ids = citydf['victimID'].values.tolist()
        male_count = citydf[citydf.gender == 'M'].shape[0]
        citykey = city.replace(' ','_') + '_' + statename
        city_entry = {
            'key': city + '_' + statename,
            'lat': lat,
            'lng': lng,
            'city': city,
            'state': statename,
            'count': citydf.shape[0],
            'male_count': male_count,
            'ids': all_ids
        }
        print(type(male_count),'????')
        citydata.append(city_entry)

# get county information
for county, countydf in data.groupby('county_name'):
    statename = countydf.iloc[0]['state_name']
    population = countydf.iloc[0]['population']
    abreviation = countydf.iloc[0]['state']
    all_ids = countydf['victimID'].values.tolist()
    # remove spaces from the state name so it's easier to use as a lookup key in jquery-style selectors later on
    county_male_count = countydf[countydf.gender == 'M'].shape[0]
    county_entry = {
        # conver np.int64 to python int for avoiding error
        'population': int(population),
        'abreviation': abreviation,
        'state': statename,
        'county': county,
        'count': countydf.shape[0],
        'male_count': county_male_count,
        'ids': all_ids
    }
    countydata.append(county_entry)
    
# look at county data
pd.DataFrame(countydata)


<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'> ????
<class 'int'

population abreviation           state       county  count  male_count  \
0         24299          SC  South Carolina    Abbeville      4           4   
1         33246          VA        Virginia     Accomack      1           1   
2        511931          ID           Idaho          Ada      3           2   
3        522140          CO        Colorado        Adams    156         108   
4        170776          SC  South Carolina        Aiken      4           3   
..          ...         ...             ...          ...    ...         ...   
849      242253          AZ         Arizona      Yavapai      6           5   
850      167146          MT         Montana  Yellowstone     12          11   
851      216986          CA      California         Yolo      1           0   
852      214591          ME           Maine         York    125         105   
853      206990          AZ         Arizona         Yuma     14          12   

                                                   ids  
0                          [3284, 11780, 11363, 13165]  
1                                              [12470]  
2                                   [2177, 3516, 4298]  
3    [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 11827, 11...  
4                           [4549, 8953, 11578, 11579]  
..                                                 ...  
849            [6690, 5295, 7970, 10661, 10670, 11925]  
850  [343, 1793, 1308, 1919, 3521, 2748, 4880, 4881...  
851                                            [11831]  
852  [444, 444, 444, 444, 444, 445, 445, 445, 445, ...  
853  [3313, 3313, 4111, 4111, 5900, 5900, 4802, 480...  

[854 rows x 7 columns]

In [8]:
pd.DataFrame(citydata).dtypes
# pd.DataFrame(countydata).dtypes

key            object
lat           float64
lng           float64
city           object
state          object
count           int64
male_count      int64
ids            object
dtype: object

In [9]:
# add city population to citydata
citiesIncounty = pd.read_csv('uscities.csv',index_col=0)
citiesIncounty = citiesIncounty[['county_name', 'population']]
citiesIncounty
for index, row in citiesIncounty.iterrows():
    city_name = index
    population = row['population']
    county_name = row['county_name']
    
    for item in citydata:
        # Check if the city name exists in citydata
        if city_name in item['city']:
            item['county'] = county_name
            item['population'] = population
citydata

[{'key': 'Anchorage_Alaska',
  'lat': 61.218056,
  'lng': -149.9002806,
  'city': 'Anchorage',
  'state': 'Alaska',
  'count': 9,
  'male_count': 9,
  'ids': [2273, 2142, 2198, 4476, 7221, 7471, 10673, 11605, 12503],
  'county': 'McLean',
  'population': 247},
 {'key': 'Sitka_Alaska',
  'lat': 57.073204,
  'lng': -135.309655601852,
  'city': 'Sitka',
  'state': 'Alaska',
  'count': 1,
  'male_count': 0,
  'ids': [472],
  'county': 'Sitka',
  'population': 8518},
 {'key': 'Albertville_Alabama',
  'lat': 34.266641,
  'lng': -86.1995994934882,
  'city': 'Albertville',
  'state': 'Alabama',
  'count': 24,
  'male_count': 24,
  'ids': [2607,
   2607,
   2607,
   2607,
   2607,
   2607,
   2607,
   2607,
   2607,
   2607,
   2607,
   2607,
   2876,
   2876,
   2876,
   2876,
   2876,
   2876,
   2876,
   2876,
   2876,
   2876,
   2876,
   2876],
  'county': 'Barton',
  'population': 132},
 {'key': 'Auburn_Alabama',
  'lat': 32.6247895,
  'lng': -85.4906763772009,
  'city': 'Auburn',
  'stat

In [10]:
#stick the dataframes into a json grouped by aggregated and unaggregated fiels
#of form {'victimID/state/city+state': {key: value, key2: value2}, {}, ...} etc
all_data = {
    'victims': data.to_dict(orient = 'records'),
    'states': statedata,
    'counties': countydata,
    'cities': citydata
}
all_data

{'victims': [{'victimID': 1,
   'date': '2012-12-14',
   'name': 'Antida Archuleta',
   'gender': 'F',
   'age': 20.0,
   'ageGroup': 3.0,
   'city': 'Westminster',
   'state': 'CO',
   'lat': 39.8936685,
   'lng': -105.072111818405,
   'url': 'http://www.9news.com/rss/story.aspx?storyid=305252',
   'year': 2012,
   'day': 14,
   'month': 12,
   'timestamp': 734851,
   'county_name': 'Adams',
   'state_name': 'Colorado',
   'population': 522140},
  {'victimID': 1,
   'date': '2012-12-14',
   'name': 'Antida Archuleta',
   'gender': 'F',
   'age': 20.0,
   'ageGroup': 3.0,
   'city': 'Westminster',
   'state': 'CO',
   'lat': 39.8936685,
   'lng': -105.072111818405,
   'url': 'http://www.9news.com/rss/story.aspx?storyid=305252',
   'year': 2012,
   'day': 14,
   'month': 12,
   'timestamp': 734851,
   'county_name': 'Adams',
   'state_name': 'Colorado',
   'population': 4625},
  {'victimID': 1,
   'date': '2012-12-14',
   'name': 'Antida Archuleta',
   'gender': 'F',
   'age': 20.0,
   

In [11]:
#save the data as a json
with open('processed_gundeaths_data.json','w') as f:
    json.dump(all_data,f)
#test that it is saved and can be read properly
with open('processed_gundeaths_data.json','r') as f:
    test = json.load(f)
test

{'victims': [{'victimID': 1,
   'date': '2012-12-14',
   'name': 'Antida Archuleta',
   'gender': 'F',
   'age': 20.0,
   'ageGroup': 3.0,
   'city': 'Westminster',
   'state': 'CO',
   'lat': 39.8936685,
   'lng': -105.072111818405,
   'url': 'http://www.9news.com/rss/story.aspx?storyid=305252',
   'year': 2012,
   'day': 14,
   'month': 12,
   'timestamp': 734851,
   'county_name': 'Adams',
   'state_name': 'Colorado',
   'population': 522140},
  {'victimID': 1,
   'date': '2012-12-14',
   'name': 'Antida Archuleta',
   'gender': 'F',
   'age': 20.0,
   'ageGroup': 3.0,
   'city': 'Westminster',
   'state': 'CO',
   'lat': 39.8936685,
   'lng': -105.072111818405,
   'url': 'http://www.9news.com/rss/story.aspx?storyid=305252',
   'year': 2012,
   'day': 14,
   'month': 12,
   'timestamp': 734851,
   'county_name': 'Adams',
   'state_name': 'Colorado',
   'population': 4625},
  {'victimID': 1,
   'date': '2012-12-14',
   'name': 'Antida Archuleta',
   'gender': 'F',
   'age': 20.0,
   

In [12]:
# certain the number of city that do not have county(Unincorporated area)
i = 0
for item in citydata:
    if ('county' not in item.keys()):
        i = i+1
        print(item)
print(i)     

0
